Notebook contenant des tests pour créer la fonction de détection de contour, notamment pour la calculer en réalisant des opérations sur les tenseurs

**/!\ Attention, utilise Keras 3** pour charger les modèles

Les modèles utilisés sont les DeepLabv3, en cas d'autres modèles, utiliser une version 2 de Keras

# Paramétrage

## Librairies

In [ ]:
# partie spécifique Google Colab
!pip install --upgrade tensorflow

     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 475.2/475.2 MB 1.8 MB/s eta 0:00:00
  Attempting uninstall: tensorflow
    Found existing installation: tensorflow 2.15.0
    Uninstalling tensorflow-2.15.0:
      Successfully uninstalled tensorflow-2.15.0


In [ ]:
# partie spécifique Google Colab
'''
If you install TensorFlow, critically, you should reinstall Keras 3 afterwards.
This is a temporary step while TensorFlow is pinned to Keras 2, and will no longer be necessary after TensorFlow 2.16.
The cause is that tensorflow==2.15 will overwrite your Keras installation with keras==2.15.
'''
!pip install --upgrade keras

     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 1.0/1.0 MB 21.3 MB/s eta 0:00:00
  Attempting uninstall: keras
    Found existing installation: keras 2.15.0
    Uninstalling keras-2.15.0:
      Successfully uninstalled keras-2.15.0
ERROR: pip's dependency resolver does not currently take into account all the packages that are installed. This behaviour is the source of the following dependency conflicts.
tensorflow 2.15.0.post1 requires keras<2.16,>=2.15.0, but you have keras 3.0.4 which is incompatible.


In [ ]:
# partie spécifique Google Colab
!pip install rasterio plotly scikit-image

     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 20.6/20.6 MB 60.0 MB/s eta 0:00:00


In [ ]:
import numpy as np
import glob
import plotly.express as px
import plotly.graph_objs as go
import cv2
import pandas as pd
import tqdm
from datetime import date
from google.colab import drive
import random
import matplotlib.pyplot as plt
import os
import math

import geopandas as gpd
import rasterio
import shapely
import skimage as ski
from skimage.measure import find_contours, approximate_polygon, subdivide_polygon, regionprops, label

from sklearn.model_selection import train_test_split
from sklearn.base import BaseEstimator, ClassifierMixin
from sklearn.ensemble import RandomForestRegressor
from sklearn.model_selection import GridSearchCV
from sklearn.metrics import mean_absolute_error, accuracy_score
from sklearn.base import TransformerMixin, BaseEstimator
from sklearn.pipeline import Pipeline

import tensorflow as tf
from tensorflow import image as tf_image
from tensorflow import data as tf_data
from tensorflow import io as tf_io

import keras
from keras import layers, Model, ops
from keras.layers import Input, Rescaling, Dense, Dropout, Flatten, Conv2D, Conv2DTranspose, \
MaxPooling2D, AveragePooling2D, SpatialDropout2D, BatchNormalization, Activation, SeparableConv2D, \
UpSampling2D, GlobalAveragePooling2D
from keras.models import Sequential, load_model
from keras.optimizers import Adam
from keras.callbacks import ReduceLROnPlateau, ModelCheckpoint
from keras.utils import load_img, img_to_array, array_to_img

import warnings
warnings.filterwarnings('ignore')


## Configuration du GPU

In [ ]:
tf.test.gpu_device_name()

'/device:GPU:0'

## Données

In [ ]:
# partie spécifique Google Colab
!mkdir -p /content/data/decoupe_final
!cp /content/drive/MyDrive/data/DST/df_decoupe_final.csv /content/data/decoupe_final/df_decoupe_final.csv
!unzip /content/drive/MyDrive/data/DST/decoupe_final.zip -d /content/data/decoupe_final

Le flux de sortie a été tronqué et ne contient que les 5000 dernières lignes.
 extracting: /content/data/decoupe_final/decoupe_final/69-2020_8_834400.0_22_6508200.0_33.cpg  
  inflating: /content/data/decoupe_final/decoupe_final/69-2020_8_834400.0_22_6508200.0_33.dbf  
  inflating: /content/data/decoupe_final/decoupe_final/69-2020_8_834400.0_22_6508200.0_33.jp2  
  inflating: /content/data/decoupe_final/decoupe_final/69-2020_8_834400.0_22_6508200.0_33.prj  
  inflating: /content/data/decoupe_final/decoupe_final/69-2020_8_834400.0_22_6508200.0_33.shp  
  inflating: /content/data/decoupe_final/decoupe_final/69-2020_8_834400.0_22_6508200.0_33.shx  
 extracting: /content/data/decoupe_final/decoupe_final/69-2020_8_834400.0_22_6508200.0_33_data.jpg  
  inflating: /content/data/decoupe_final/decoupe_final/69-2020_8_834400.0_22_6508200.0_33_data.jpg.aux.xml  
  inflating: /content/data/decoupe_final/decoupe_final/69-2020_8_834400.0_22_6508200.0_33_label.png  
  inflating: /content/data/decoupe

In [ ]:
data_path = '/content/data/decoupe_final'
images_path = '/content/data/decoupe_final/decoupe_final'
df_decoupe = pd.read_csv(data_path + '/df_decoupe_final.csv')
df_decoupe.head()

dalle_X  dalle_Y         X          Y  X_size  Y_size  \
0        0        0  825000.0  6509800.0    1000    1000   
1        0        1  825000.0  6509600.0    1000    1000   
2        0        2  825000.0  6509400.0    1000    1000   
3        0        3  825000.0  6509200.0    1000    1000   
4        0        4  825000.0  6509000.0    1000    1000   

                          fichier_raster  \
0   69-2020_0_825000.0_0_6509800.0_0.jp2   
1   69-2020_1_825000.0_0_6509600.0_0.jp2   
2   69-2020_2_825000.0_0_6509400.0_4.jp2   
3   69-2020_3_825000.0_0_6509200.0_4.jp2   
4  69-2020_4_825000.0_0_6509000.0_19.jp2   

                                  fichier_img  \
0   69-2020_0_825000.0_0_6509800.0_0_data.jpg   
1   69-2020_1_825000.0_0_6509600.0_0_data.jpg   
2   69-2020_2_825000.0_0_6509400.0_4_data.jpg   
3   69-2020_3_825000.0_0_6509200.0_4_data.jpg   
4  69-2020_4_825000.0_0_6509000.0_19_data.jpg   

                                  fichier_mask  \
0   69-2020_0_825000.0_0_6509800.0_0_label.png   
1   69-2020_1_825000.0_0_6509600.0_0_label.png   
2   69-2020_2_825000.0_0_6509400.0_4_label.png   
3   69-2020_3_825000.0_0_6509200.0_4_label.png   
4  69-2020_4_825000.0_0_6509000.0_19_label.png   

                          fichier_shapes  formes  multi  erreur  
0   69-2020_0_825000.0_0_6509800.0_0.shp       0      0       0  
1   69-2020_1_825000.0_0_6509600.0_0.shp       0      0       0  
2   69-2020_2_825000.0_0_6509400.0_4.shp       4      0       0  
3   69-2020_3_825000.0_0_6509200.0_4.shp       4      0       0  
4  69-2020_4_825000.0_0_6509000.0_19.shp      19      0       0

## Fonctions

In [ ]:
def read_image(image_path, mask = False, resnet50_preprocess = True):
  image = tf_io.read_file(image_path)
  if mask:
    image = tf_image.decode_png(image, channels = 1)
    if BINARY_MASK:
      image = tf.where(tf.math.greater(image, 0), 1, 0)
    image.set_shape([None, None, 1])
    image = tf_image.resize(images = image, size = RESOLUTION)
  else:
    image = tf_image.decode_png(image, channels = 3)
    image.set_shape([None, None, 3])
    image = tf_image.resize(images = image, size = RESOLUTION)
    if resnet50_preprocess:
      # on reproduit le résultat de la fonction tf.keras.applications.resnet50.preprocess_input
      image = image[..., ::-1] - tf.constant(PIXEL_MEAN)
  return image


In [ ]:
def predict_deeplabv3(file_name, model, seuil):
  img_reduite = read_image(file_name)
  prevision_raw = np.squeeze(model.predict(tf.expand_dims(img_reduite, 0), verbose = 0))
  prevision = np.sum(prevision_raw[:,:,1:], -1)
  prevision = np.where(prevision > seuil, 1, 0)
  return [prevision]

In [ ]:
def calcul_ious_shapes(shapes_1_ext, shapes_2_ext):
  '''
  fonction qui calcule l'IoU des shapes_1_ext en cherchant à rapprocher les shapes_2_ext
  renvoie la liste des ious calculés
  '''
  ious = []
  rapprochements = []
  for i in range(len(shapes_1_ext)):
    shape_1 = shapely.Polygon(shapes_1_ext[i])
    unions = []
    unions.append(shape_1)
    intersections = []
    for j in range(len(shapes_2_ext)):
      shape_2 = shapely.Polygon(shapes_2_ext[j])
      if shape_2 is not None:
        if shape_1.intersects(shape_2):
          intersection = shape_1.intersection(shape_2)
          intersections.append(intersection)
          unions.append(shape_2)
    if len(intersections) > 0:
      intersection_area = shapely.area(gpd.GeoSeries(intersections, crs = 2154).unary_union)
    else:
      intersection_area = 0
    union_area = shapely.area(gpd.GeoSeries(unions, crs = 2154).unary_union)
    if union_area == 0:
      ious.append(0)
    else:
      ious.append(intersection_area/union_area)
    rapprochements.append(len(intersections))
  return ious, rapprochements

In [ ]:
def affiche_contours(
    model, predict_function, df, chemin_images, index_l, resolution_model, resolution_target = (1000, 1000),
    seuil = None, seuil_iou = 0, gdf_shapes_ref = None, affichage = True,
    seuil_area = 10,
    tolerance_polygone = 0.1):
  '''
  fonction qui calcule les IoU des formes prédites par rapport à des formes de référence
  utilise les mêmes arguements que compare_ligne, avec en plus :
  - predict_function : fonction qui prend en argument le triplet (file_name, model, seuil) et qui renvoie la prévision du modèle "model" avec les dimensions correspondant
  au paramètre "resolution_model", pour le seuil de détection "seuil"
  - seuil_iou : les formes avec un IoU inférieur sont affichées en rouge
  - gdf_shapes_ref : fichier de shapefiles à utiliser pour la comparaison des formes prédites > par défaut, on compare par rapport aux formes du df_decoupe
  renvoie :
  - geoSeries avec les formes prédites, crs 2154, avec uniquement les contours
  - geoSeries avec les formes de réference, crs 2154, avec uniquement les contours
  - shapes_pred_ious, ious des formes prédites par rapport aux formes de référence
  - shapes_ref_ious, ious des formes de référence par rapport aux formes prédites
  - shapes_pred_rapprochements, nombre de formes de référence rapprochées pour chaque forme prédite
  - shapes_ref_rapprochements, nombre de formes prédites rapprochées pour chaque forme de référence
  '''
  file_name = chemin_images + df.loc[index_l,'fichier_img']
  raster_name = chemin_images + df.loc[index_l, 'fichier_raster']
  shape_name = chemin_images + df.loc[index_l, 'fichier_shapes']

  # Prévision
  prev_masks = predict_function(file_name, model, seuil)
  # Contours prédiction
  mask_contours = []
  for prev_mask in prev_masks:
    prev_mask_resized = tf.squeeze(tf_image.resize(images = np.expand_dims(prev_mask, -1), size = resolution_target, method = 'nearest'))
    mask_padded = np.pad(prev_mask_resized, ((1, 1),(1, 1)), mode = 'constant', constant_values = 0)
    mask_contours += ski.measure.find_contours(image = mask_padded == 1)

  # Shapes prédiction
  with rasterio.open(raster_name) as raster:
    # création du convertisseur pour passer des coordonnées en pixels
    raster_transform = raster.transform
    raster_transformer = rasterio.transform.AffineTransformer(raster_transform)
    shapes_xy = []
    shapes_predict = []
    # parcours de tous les contours prédits
    for contour in mask_contours:
      # on crée le polygone
      polygon = approximate_polygon(contour, tolerance = tolerance_polygone)
      # on tranforme en coordonnées
      xy_polygon = raster_transformer.xy(polygon[:,0], polygon[:,1])
      shapes_xy.append(xy_polygon)
      # on crée le polygone
      shapes_predict.append(shapely.Polygon(np.array(xy_polygon).transpose()))
  # on filtre les surface trop petites
  shapes_predict = [shape for shape in shapes_predict if shapely.area(shape) > seuil_area]
  # Ajout des trous dans les shapes prédiction
  shapes_predict_holes = []
  shapes_holes = []
  for shape_a in shapes_predict:
    if shape_a not in shapes_holes:
      shape_a_holes = []
      for shape_b in shapes_predict:
        if shape_a.contains_properly(shape_b):
          shape_a_holes.append(shape_b.exterior)
          shapes_holes.append(shape_b)
      if len(shape_a_holes) > 0:
        shapes_predict_holes.append(shapely.Polygon(shape_a.exterior, holes = shape_a_holes))
      else:
        shapes_predict_holes.append(shape_a)
  gdf_shapes_predict = gpd.GeoDataFrame(geometry = gpd.GeoSeries(shapes_predict_holes, crs=2154), crs=2154)
  # gdf_shapes_predict = gdf_shapes_predict[gdf_shapes_predict['geometry'].is_valid].reset_index()

  # Shapes référence
  if gdf_shapes_ref is None:
    gdf_shapes_ref = gpd.read_file(shape_name)
  # gdf_shapes_ref = gdf_shapes_ref[gdf_shapes_ref['geometry'].is_valid].reset_index()
  # /!\ on court-circuite le traitement pour éviter de supprimer des formes de référence
  '''
  # Regroupement et fusion des formes adjacentes
  gdf_shapes_ref['group'] = ''
  for index in range(gdf_shapes_ref.shape[0]):
    group = gdf_shapes_ref[~gdf_shapes_ref.geometry.disjoint(gdf_shapes_ref.geometry[index])].index.to_list()
    if len(group) > 1:
      if gdf_shapes_ref.loc[index, 'group'] == '':
        gdf_shapes_ref.loc[group, 'group'] = 'group_' + str(index)
      else:
        gdf_shapes_ref.loc[group, 'group'] = gdf_shapes_ref.loc[index, 'group']
  gdf_shapes_ref_merged = gdf_shapes_ref.dissolve(by = 'group', as_index = False)
  gdf_shapes_ref_merged = gdf_shapes_ref_merged[gdf_shapes_ref_merged['geometry'].is_valid].reset_index()
  '''

  # Intersection et IoUs
  shapes_ref = gdf_shapes_ref['geometry'].exterior
  shapes_ref = [shape for shape in shapes_ref if shape is not None]
  shapes_predict = gdf_shapes_predict['geometry'].exterior
  shapes_predict = [shape for shape in shapes_predict if shape is not None]
  # iou des prédictions
  shapes_pred_ious, shapes_pred_rapprochements = calcul_ious_shapes(shapes_predict, shapes_ref)
  # iou des réferences
  shapes_ref_ious, shapes_ref_rapprochements = calcul_ious_shapes(shapes_ref, shapes_predict)

  fig = None
  if affichage:
    # lecture du raster
    raster_file = chemin_images + df.loc[index_l,'fichier_raster']
    with rasterio.open(raster_file) as raster:
        bounds = raster.bounds
        raster_data = np.transpose(raster.read(), [1,2,0])

    # génération du graphique
    X0 = df.loc[index_l, 'X']
    Y0 = df.loc[index_l, 'Y']
    dalle_X = df.loc[index_l, 'dalle_X']
    dalle_Y = df.loc[index_l, 'dalle_Y']
    nb_formes = df.loc[index_l, 'formes']
    fig = px.imshow(
        cv2.flip(raster_data, 0),
        x = np.linspace(bounds.left, bounds.right, raster.width),
        y = np.linspace(bounds.bottom, bounds.top, raster.height),
        title = 'Image {}, {} ({}, {})<br>{} bâtiments<br>fichier {}<br>{} zones détectées'.format(
            str(X0), str(Y0), str(dalle_X), str(dalle_Y), str(nb_formes), raster_file,
            np.sum((np.array(shapes_pred_ious) <= seuil_iou) & (np.array(shapes_pred_rapprochements) == 0))),
        origin = 'lower')
    # ajout des formes
    shape_traces_to_plot = []
    # formes de référence
    for shape, iou, rapprochement in zip(shapes_ref, shapes_ref_ious, shapes_ref_rapprochements):
      list_x, list_y = shape.xy
      shape_traces_to_plot.append(
          go.Scatter(
              x = np.array(list_x),
              y = np.array(list_y),
              line = dict(color='black', width=1),
              mode = 'lines',
              fill = 'toself',
              fillcolor = '#80b1d3',
              opacity = 0.4,
              text = 'iou référence: {}<br>{} prédictions rapprochées'.format(iou, rapprochement),
              hoverinfo = 'text',
              showlegend = False))
    # formes prédites
    for shape, iou, rapprochement in zip(shapes_predict, shapes_pred_ious, shapes_pred_rapprochements):
      if iou <= seuil_iou and rapprochement == 0:
        color_shape = 'red'
      else:
        color_shape = '#ffed6f'
      list_x, list_y = shape.xy
      shape_traces_to_plot.append(
          go.Scatter(
              x = np.array(list_x),
              y = np.array(list_y),
              line = dict(color='black', width=1),
              mode = 'lines',
              fill = 'toself',
              fillcolor = color_shape,
              opacity = 0.4,
              text = 'iou prédiction: {}<br>{} bâtiments rapprochés'.format(iou, rapprochement),
              hoverinfo = 'text',
              showlegend = False))
    fig.add_traces(shape_traces_to_plot)
    # mise en forme
    fig.update_layout(
        xaxis=dict(title='X en Lambert93'),
        yaxis=dict(title='Y en Lambert93'),
        plot_bgcolor='white',
        height = 900,
        width = 900)

  return shapes_predict, shapes_ref, shapes_pred_ious, shapes_ref_ious, shapes_pred_rapprochements, shapes_ref_rapprochements, fig


# Détection de contours

In [ ]:
model = load_model('/content/drive/MyDrive/DataScientest/Keras/DeeplabV3Plus_model_20240107.keras')

In [ ]:
SIZE = 512
RESOLUTION = (SIZE, SIZE)
NUM_CLASSES = 2
BINARY_MASK = True
BATCH_SIZE = 16
SEED = 77
PIXEL_MEAN = [103.939, 116.779, 123.68]

In [ ]:
_, df_contours = train_test_split(df_decoupe, test_size=0.2, random_state=SEED)
df_contours = df_contours.reset_index()

In [ ]:
gdf_shapes_predict_holes_ext, gdf_shapes_ref_merged_ext, shapes_pred_ious, shapes_ref_ious, _, _, fig = affiche_contours(
    model, predict_deeplabv3, df_decoupe, images_path + '/', 899,
    RESOLUTION, resolution_target = (1000, 1000),
    seuil = 0.85, seuil_iou = 0.01, gdf_shapes_ref = None, affichage = True,
    seuil_area = 30)
fig.show()

In [ ]:
# liste d'images à tester
list_index_contours_test = [4275, 7475, 3610, 6286, 3462, 6337, 7362, 2663, 3438, 6838, 4439, 4339, 6864, 6890, 4341, 4192, 6267, 6592, 7393, 7244, 7419, 1801, 7426, 720, 7420, 6723, 899, 349, 3349, 4424, 7174, 2052, 2777, 7377, 7402, 6177, 3328, 1129, 4429, 6779, 3730, 4430, 6433, 7358, 2359, 3934, 6284]
for i in tqdm.tqdm(list_index_contours_test):
  _, _, shapes_pred_ious, shapes_ref_ious, _, _, fig = affiche_contours(
      model, predict_deeplabv3, df_decoupe, images_path + '/', i,
      RESOLUTION, resolution_target = (1000, 1000),
      seuil = 0.85, seuil_iou = 0.01, gdf_shapes_ref = None, affichage = True,
      seuil_area = 30)
  fig.write_html('/content/drive/MyDrive/DataScientest/Keras/DeeplabV3Plus_model_20240107_contour_{}.html'.format(i))


100%|██████████| 47/47 [01:08<00:00,  1.46s/it]


In [ ]:
pred_dict = {
    'pred_ious':[],
    'ref_ious':[],
    'pred_rapprochements':[],
    'ref_rapprochements':[]
}
for i in tqdm.tqdm(range(df_decoupe.shape[0])):
  _, _, pred_ious, ref_ious, pred_rapprochements, ref_rapprochements, _ = affiche_contours(
      model, predict_deeplabv3, df_decoupe, images_path + '/', i,
      RESOLUTION, resolution_target = (1000, 1000),
      seuil = 0.85, seuil_iou = 0.01, gdf_shapes_ref = None, affichage = False,
      seuil_area = 30)
  pred_dict['pred_ious'] += pred_ious
  pred_dict['ref_ious'] += ref_ious
  pred_dict['pred_rapprochements'] += pred_rapprochements
  pred_dict['ref_rapprochements'] += ref_rapprochements


100%|██████████| 7500/7500 [1:08:41<00:00,  1.82it/s]


In [ ]:
df_pred_pred = pd.DataFrame({'pred_ious':pred_dict['pred_ious'], 'pred_rapprochements':pred_dict['pred_rapprochements']})
df_pred_pred.to_csv('/content/drive/MyDrive/DataScientest/Keras/DeeplabV3Plus_model_20240107_contour_pred.csv',
                    index = False)

In [ ]:
df_pred_ref = pd.DataFrame({'ref_ious':pred_dict['ref_ious'], 'ref_rapprochements':pred_dict['ref_rapprochements']})
df_pred_ref.to_csv('/content/drive/MyDrive/DataScientest/Keras/DeeplabV3Plus_model_20240107_contour_ref.csv',
                    index = False)

In [ ]:
np.mean(pred_dict['pred_ious'])

0.6771147104097353

In [ ]:
px.histogram(pred_dict['pred_ious'])

# Calcul IoUs avec tenseurs

In [ ]:
def read_mask(image_path):
  image = tf_io.read_file(image_path)
  image = tf_image.decode_png(image, channels = 1)
  if BINARY_MASK:
    image = tf.where(tf.math.greater(image, 0), 1, 0)
  image.set_shape([None, None, 1])
  image = tf_image.resize(images = image, size = RESOLUTION, method = 'nearest')
  return image

In [ ]:
SIZE = 512
RESOLUTION = (SIZE, SIZE)
BINARY_MASK = True
SEED = 77

df_train, df_test = train_test_split(df_decoupe, test_size=0.2, random_state = SEED)
df_decoupe_0bat = df_decoupe[df_decoupe['formes'] == 0]
df_decoupe_1bat = df_decoupe[df_decoupe['formes'] == 1]
df_decoupe_10bat = df_decoupe[df_decoupe['formes'] == 10]

In [ ]:
mask_data1 = tf.squeeze(read_mask(images_path + '/' + df_decoupe_1bat['fichier_mask'].values[69]))
mask_data2 = tf.squeeze(read_mask(images_path + '/' + df_decoupe_1bat['fichier_mask'].values[39]))
mask_data3 = tf.squeeze(read_mask(images_path + '/' + df_decoupe_1bat['fichier_mask'].values[89]))
mask_data4 = tf.squeeze(read_mask(images_path + '/' + df_decoupe_1bat['fichier_mask'].values[87]))[:,::-1]
mask_data_all = tf.stack([mask_data1, mask_data2, mask_data3, mask_data4])
mask_data_all_bis = tf.stack([mask_data2, mask_data4])

## Tests avec 1 seul bâtiment

In [ ]:
a = tf.constant([[[1, 0], [0, 1]], [[3, 0], [0, 3]]])
b = tf.constant([7, 8, 9, 10, 11, 12], shape = [6, 1])
c = tf.constant([7, 8, 9, 10, 11, 12], shape = [1, 6])

In [ ]:
x = tf.einsum('ixy,jxy->ijxy', mask_data_all, mask_data_all)
x.shape

TensorShape([4, 4, 512, 512])

In [ ]:
px.imshow(x[1, 3, :, :].numpy()*255)

In [ ]:
px.imshow(y[1, 3, :, :].numpy()*255)

In [ ]:
px.imshow((x/y)[1, 3, :, :].numpy()*255)

In [ ]:
calcul_iou_PR(mask_data_all, mask_data_all_bis, 0)

(1,
 0.8,
 <tf.Tensor: shape=(4, 2), dtype=float64, numpy=
 array([[0.       , 0.       ],
        [1.       , 0.3225357],
        [0.       , 0.       ],
        [0.3225357, 1.       ]])>)

## Test avec 10 bâtiments

In [ ]:
mask_data_10_1 = tf.squeeze(read_mask(images_path + '/' + df_test['fichier_mask'].values[40]))
px.imshow(label(mask_data_10_1)+1)

In [ ]:
mask_data_0_1 = tf.squeeze(read_mask(images_path + '/' + df_decoupe_0bat['fichier_mask'].values[4]))
label_mask, num_labels = label(mask_data_0_1, return_num = True)

In [ ]:
px.imshow(tf.where(label_mask == 6, 1, 0))

In [ ]:
label_mask_ref, num_labels_ref = label(mask_data_10_1, return_num = True)
pred_mask_list = [tf.where(label_mask == i, 1, 0) for i in [1, 2, 3, 6]]
TP, FP, FN, precision, recall, intersections, unions, ious = calcul_iou_PR_inseg(
    mask_data_10_1,
    pred_mask_list,
    0.5)

## Fonctions

In [ ]:
def calcul_iou_PR_seg(tf_mask_list_ref, tf_mask_list_pred, iou_seuil):
  '''
  calcul des métriques entre deux listes de masques
  tf_mask_list_ref et tf_mask_list_pred sont des listes de R et P tenseurs de dimension (D, D)
  renvoie :
  - recall
  - precision
  - matrice des IoUs sous forme de tenseur de dimension (R, D)
  '''
  # on transforme chaque liste de tenseurs en tenseurs de dimension (R, D, D) et (P, D, D)
  tf_mask_ref_all = tf.stack(tf_mask_list_ref)
  tf_mask_pred_all = tf.stack(tf_mask_list_pred)

  # l'intersection est calculée pixel par pixel en multiplicant les valeurs pixel à pixel
  # grâce à l'outer product sur les deux tenseurs (P, D, D) et (R, D, D)
  # on obtient un tenseur de dimension (R, P, D, D)
  masks_intersections = tf.einsum('ixy,jxy->ijxy', tf_mask_ref_all, tf_mask_pred_all)

  # l'union est calculée pixel par pixel en broadcastant les tenseurs des masques prédits (P, D, D)
  # sur les tenseurs des masques de référence (R, D, D)
  # on obtient un tenseur de dimension (R, P, D, D)
  masks_unions = tf.clip_by_value(tf.expand_dims(tf_mask_ref_all, 1) + tf_mask_pred_all, 0, 1)

  # calcul du nombre de pixels pour chaque intersection (R, D)
  intersections = tf.reduce_sum(masks_intersections, axis = [2, 3])

  # calcul du nombre de pixels pour chaque union (R, D)
  unions = tf.reduce_sum(masks_unions, axis = [2, 3])

  # calcul du nombre de pixels des masques : tenseurs de dimension (R) et (P)
  refs = tf.reduce_sum(tf_mask_ref_all, axis = [1, 2])
  preds = tf.reduce_sum(tf_mask_pred_all, axis = [1, 2])

  # calcul des IoUs : le résultat est un tenseur de dimension (R, D)
  ious = intersections/unions

  # true positives : si le masque prédit n'est pas vide, et que l'IoU est au-dessus du seuil
  TP = tf.boolean_mask(ious >= iou_seuil, preds > 0, axis = 1).numpy().sum()
  # false positives : si le masque prédit n'est pas vide, et que l'IoU est en-dessous du seuil
  FP = tf.boolean_mask(ious < iou_seuil, preds > 0, axis = 1).numpy().sum()
  # false negatives : si le masque de référence n'est pas vide et que tous ses IoUs sont à 0
  FN = np.sum(tf.boolean_mask(ious == 0, refs > 0, axis = 0).numpy().sum(axis = 1) == 0)

  # recall = 1 when FN=0, since 100% of the TP were discovered
  if FN == 0:
    recall = 1
  else:
    recall = TP/(TP + FN)

  # precision = 1 when FP=0, since there were no spurious results
  if FP == 0:
    precision = 1
  else:
    precision = TP/(TP + FP)

  return precision, recall, ious

In [ ]:
def calcul_iou_PR_inseg(
    model, predict_function,
    df, chemin_images, index_l, resolution_model,
    seuil = None, seuil_iou = 0):
  '''
  calcul des métriques entre deux listes de masques
  tf_mask_ref est le masque de référence de dimension (D, D), il est transformé en une listes de R tenseurs,
  R étant le nombre de formes connexes
  tf_mask_list_pred est la listes de P tenseurs de dimension (D, D)
  renvoie :
  - true positives
  - false positives
  - false negatives
  - precision
  - recall
  - matrice des intersections masque à masque
  - matrice des unions masque à masque
  - matrice des IoUs sous forme de tenseur de dimension (R, D)
  '''

  # Prévision
  file_name = chemin_images + df.loc[index_l,'fichier_img']
  tf_mask_list_pred = predict_function(file_name, model, seuil)
  # on transforme la liste des tenseurs prédits en tenseur de dimension (P, D, D)
  tf_mask_pred_all = tf.stack(tf_mask_list_pred)
  tf_mask_pred_all = tf.cast(tf_mask_pred_all, tf.int32)

  # Référence
  def read_mask(image_path):
    image = tf_io.read_file(image_path)
    image = tf_image.decode_png(image, channels = 1)
    image = tf.where(tf.math.greater(image, 0), 1, 0)
    image.set_shape([None, None, 1])
    image = tf.squeeze(tf_image.resize(images = image, size = resolution_model, method = 'nearest'))
    return image
  mask_name = chemin_images + df.loc[index_l, 'fichier_mask']
  tf_mask_ref = read_mask(mask_name)
  # on découpe le masque de référence en formes connexes pour avoir un tenseur de dimension (R, D, D)
  label_mask_ref, num_labels_ref = label(tf_mask_ref, return_num = True)
  if num_labels_ref == 0:
    tf_mask_ref_all = tf.zeros((1,) + resolution_model)
  else:
    tf_mask_ref_all = tf.cast(
        tf.stack([tf.where(label_mask_ref == label_num, 1, 0) for label_num in range(1, num_labels_ref + 1)]),
        tf.int32)

  # l'intersection est calculée pixel par pixel en multiplicant les valeurs pixel à pixel
  # grâce à l'outer product sur les deux tenseurs (P, D, D) et (R, D, D)
  # on obtient un tenseur de dimension (R, P, D, D)
  masks_intersections = tf.einsum('ixy,jxy->ijxy', tf_mask_ref_all, tf_mask_pred_all)
  # calcul du nombre de pixels pour chaque intersection (R, D)
  intersections = tf.reduce_sum(masks_intersections, axis = [2, 3])

  # l'union est calculée pixel par pixel en broadcastant les tenseurs des masques prédits (P, D, D)
  # sur les tenseurs des masques de référence (R, D, D)
  # on obtient un tenseur de dimension (R, P, D, D)
  masks_unions = tf.clip_by_value(tf.expand_dims(tf_mask_ref_all, 1) + tf_mask_pred_all, 0, 1)
  # calcul du nombre de pixels pour chaque union (R, D)
  unions = tf.reduce_sum(masks_unions, axis = [2, 3])

  # calcul du nombre de pixels des masques : tenseurs de dimension (R) et (P)
  refs = tf.reduce_sum(tf_mask_ref_all, axis = [1, 2])
  preds = tf.reduce_sum(tf_mask_pred_all, axis = [1, 2])

  # calcul des IoUs : le résultat est un tenseur de dimension (R, D)
  ious = intersections/unions

  # true positives : si le masque prédit n'est pas vide, et que l'IoU est au-dessus du seuil
  TP = tf.boolean_mask(ious >= seuil_iou, preds > 0, axis = 1).numpy().sum()
  # false positives : si le masque prédit n'est pas vide, et que l'IoU est en-dessous du seuil
  FP = tf.boolean_mask(ious < seuil_iou, preds > 0, axis = 1).numpy().sum()
  # false negatives : si le masque de référence n'est pas vide et que tous ses IoUs sont à 0
  FN = np.sum(tf.boolean_mask(ious == 0, refs > 0, axis = 0).numpy().sum(axis = 1) == 0)

  # recall = 1 when FN=0, since 100% of the TP were discovered
  if FN == 0:
    recall = 1
  else:
    recall = TP/(TP + FN)

  # precision = 1 when FP=0, since there were no spurious results
  if FP == 0:
    precision = 1
  else:
    precision = TP/(TP + FP)

  return TP, FP, FN, precision, recall, intersections, unions, ious

## Brouillons

In [ ]:
# /!\ ANCIENNE FONCTION
def calcul_iou_PR_inseg(tf_mask_ref, tf_mask_list_pred, iou_seuil):
  '''
  calcul des métriques entre deux listes de masques
  tf_mask_ref est le masque de référence de dimension (D, D), il es transformé en une listes de R tenseurs,
  R étant le nombre de formes connexes
  tf_mask_list_pred est la listes de P tenseurs de dimension (D, D)
  renvoie :
  - true positives
  - false positives
  - false negatives
  - precision
  - recall
  - matrice des intersections masque à masque
  - matrice des unions masque à masque
  - matrice des IoUs sous forme de tenseur de dimension (R, D)
  '''
  # on découpe le masque de référence en formes
  label_mask_ref, num_labels_ref = label(tf_mask_ref, return_num = True)
  tf_mask_ref_all = tf.stack([tf.where(label_mask_ref == label_num, 1, 0) for label_num in range(1, num_labels_ref + 1)])
  # on transforme la liste des tenseurs prédits en tenseurs de dimension (R, D, D) et (P, D, D)
  tf_mask_pred_all = tf.stack(tf_mask_list_pred)

  # l'intersection est calculée pixel par pixel en multiplicant les valeurs pixel à pixel
  # grâce à l'outer product sur les deux tenseurs (P, D, D) et (R, D, D)
  # on obtient un tenseur de dimension (R, P, D, D)
  masks_intersections = tf.einsum('ixy,jxy->ijxy', tf_mask_ref_all, tf_mask_pred_all)
  # calcul du nombre de pixels pour chaque intersection (R, D)
  intersections = tf.reduce_sum(masks_intersections, axis = [2, 3])

  # l'union est calculée pixel par pixel en broadcastant les tenseurs des masques prédits (P, D, D)
  # sur les tenseurs des masques de référence (R, D, D)
  # on obtient un tenseur de dimension (R, P, D, D)
  masks_unions = tf.clip_by_value(tf.expand_dims(tf_mask_ref_all, 1) + tf_mask_pred_all, 0, 1)
  # calcul du nombre de pixels pour chaque union (R, D)
  unions = tf.reduce_sum(masks_unions, axis = [2, 3])

  # calcul du nombre de pixels des masques : tenseurs de dimension (R) et (P)
  refs = tf.reduce_sum(tf_mask_ref_all, axis = [1, 2])
  preds = tf.reduce_sum(tf_mask_pred_all, axis = [1, 2])

  # calcul des IoUs : le résultat est un tenseur de dimension (R, D)
  ious = intersections/unions

  # true positives : si le masque prédit n'est pas vide, et que l'IoU est au-dessus du seuil
  TP = tf.boolean_mask(ious >= iou_seuil, preds > 0, axis = 1).numpy().sum()
  # false positives : si le masque prédit n'est pas vide, et que l'IoU est en-dessous du seuil
  FP = tf.boolean_mask(ious < iou_seuil, preds > 0, axis = 1).numpy().sum()
  # false negatives : si le masque de référence n'est pas vide et que tous ses IoUs sont à 0
  FN = np.sum(tf.boolean_mask(ious == 0, refs > 0, axis = 0).numpy().sum(axis = 1) == 0)

  # recall = 1 when FN=0, since 100% of the TP were discovered
  if FN == 0:
    recall = 1
  else:
    recall = TP/(TP + FN)

  # precision = 1 when FP=0, since there were no spurious results
  if FP == 0:
    precision = 1
  else:
    precision = TP/(TP + FP)

  return TP, FP, FN, precision, recall, intersections, unions, ious